## Import Libaries

In [127]:
import numpy as np

# create strategy
import pandas_ta as ta

# backtesting library
import vectorbt as vbt

# get data from TradingView
from tvDatafeed import TvDatafeed, Interval
tv = TvDatafeed()

## Import Data

In [128]:
raw_df = tv.get_hist(symbol='BTCUSDT',exchange='BINANCE',interval=Interval.in_1_hour ,n_bars=100000)
raw_df

symbol      open      high       low     close  \
datetime                                                                       
2022-01-01 07:00:00  BINANCE:BTCUSDT  46216.93  46731.39  46208.37  46656.13   
2022-01-01 08:00:00  BINANCE:BTCUSDT  46656.14  46949.99  46574.06  46778.14   
2022-01-01 09:00:00  BINANCE:BTCUSDT  46778.14  46928.94  46721.96  46811.77   
2022-01-01 10:00:00  BINANCE:BTCUSDT  46811.77  46916.63  46760.12  46813.20   
2022-01-01 11:00:00  BINANCE:BTCUSDT  46813.21  46887.33  46591.23  46711.05   
...                              ...       ...       ...       ...       ...   
2023-03-31 16:00:00  BINANCE:BTCUSDT  27797.31  27878.84  27770.00  27819.99   
2023-03-31 17:00:00  BINANCE:BTCUSDT  27820.00  27992.05  27798.48  27893.80   
2023-03-31 18:00:00  BINANCE:BTCUSDT  27893.81  27980.00  27842.10  27927.97   
2023-03-31 19:00:00  BINANCE:BTCUSDT  27927.97  28185.63  27870.93  28110.36   
2023-03-31 20:00:00  BINANCE:BTCUSDT  28110.37  28224.08  28082.71  28187.49   

                         volume  
datetime                         
2022-01-01 07:00:00  1503.33095  
2022-01-01 08:00:00   943.81539  
2022-01-01 09:00:00   485.16860  
2022-01-01 10:00:00   562.88971  
2022-01-01 11:00:00   861.88389  
...                         ...  
2023-03-31 16:00:00  2456.37429  
2023-03-31 17:00:00  2535.91766  
2023-03-31 18:00:00  2250.15003  
2023-03-31 19:00:00  5284.54573  
2023-03-31 20:00:00  1096.43050  

[10908 rows x 6 columns]

## Create Strategy

In [129]:
strategy_name = "Demo Strategy"
strategy1 = ta.Strategy(
    name='Demo Strategy',
    description='',
    ta=[
        {
            'kind': 'adx', 'length': 14
            , 'col_names': ('ADX_14', 'DMP_14', 'DMN_14')
            
        },
        {
            'kind': 'bbands', 'length': 20, 'std': 3, 
            'col_names': ('BBL', 'BBM', 'BBU', 'BBB', 'BBP')
        },
        {
            'kind': 'ema', 'length': 200
            , 'col_names': ('EMA')
        },
        {
            "kind": "donchian", "lower_length": 12, "upper_length": 24
            , "col_names": ("DCL", "DCM", "DCU")
        }
    ]
)

strat1 = raw_df.copy()
strat1.ta.strategy(strategy1)

# CREATE SIGNAL
strat1['LONG_ENTRIES'] = (
    (~strat1.isna().any(axis=1))
    & (strat1['ADX_14'] > 50)
    & (strat1['close'] > strat1['EMA'])
    & (ta.cross_value(strat1["high"], strat1["DCU"].shift(),  above=True, asint=False))
)

strat1['LONG_EXITS'] = (
    (~strat1.isna().any(axis=1))
    & (strat1['low'] < strat1['BBU'].shift())
)

strat1['SHORT_ENTRIES'] = (
    (~strat1.isna().any(axis=1))
    & (strat1['ADX_14'] > 50)
    & (strat1['close'] < strat1['EMA'])
    & (ta.cross_value(strat1["low"], strat1["DCL"].shift(),  above=False, asint=False))
)

strat1['SHORT_EXITS'] = (
    (~strat1.isna().any(axis=1))
    & (strat1['high'] > strat1['BBU'].shift())
)

# more realistic entry signal
strat1['LONG_ENTRIES'] = strat1['LONG_ENTRIES'].shift(1).replace(np.nan, False)
strat1['LONG_EXITS'] = strat1['LONG_EXITS'].shift(1).replace(np.nan, False)
strat1['SHORT_ENTRIES'] = strat1['SHORT_ENTRIES'].shift(1).replace(np.nan, False)
strat1['SHORT_EXITS'] = strat1['SHORT_EXITS'].shift(1).replace(np.nan, False)

port = vbt.Portfolio.from_signals(strat1.open,
                                entries = strat1['LONG_ENTRIES'],
                                exits= strat1['LONG_EXITS'],
                                short_entries = strat1['SHORT_ENTRIES'],
                                short_exits= strat1['SHORT_EXITS'],
                                freq = '1h',
                                init_cash = 1000,
                                size=0.1,
                                fees = 0.0002,
                                slippage = 0.005,
                                 )
port.plot().show()

port.stats()

Start                         2022-01-01 07:00:00
End                           2023-03-31 20:00:00
Period                          454 days 12:00:00
Start Value                                1000.0
End Value                             2135.850611
Total Return [%]                       113.585061
Benchmark Return [%]                   -39.177332
Max Gross Exposure [%]                 111.417119
Total Fees Paid                         11.055069
Max Drawdown [%]                        22.817285
Max Drawdown Duration           147 days 10:00:00
Total Trades                                   10
Total Closed Trades                            10
Total Open Trades                               0
Open Trade PnL                                0.0
Win Rate [%]                                 50.0
Best Trade [%]                          16.723029
Worst Trade [%]                         -3.381751
Avg Winning Trade [%]                    8.992108
Avg Losing Trade [%]                    -1.725157
